In [2]:
import pyodbc
import configparser
import pandas as pd
import numpy as np
from datetime import datetime, time
 
 
config = configparser.ConfigParser()
config.read("credenciais_banco.ini")
 
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")
 
#gerar query
query_base_dados= '''
select * from draft_historico dh 
left join ciclos_data_2025 cd on cd.[Date] = dh.data
where dh.brandgroupcode = 'EUD' and dh.codcategory not in ('SUPORTE À VENDA','EMBALAGENS', 'GIFTS') 
and dh.description not like ('PRM') and dh.data in ('2025-06-25','2025-07-16','2025-08-06','2025-08-27','2025-09-17') and cd.MARCA ='EUD'
'''
df_base = pd.read_sql(query_base_dados, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\1591507404.py:26: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_base = pd.read_sql(query_base_dados, conn)


In [3]:
import pyodbc
import configparser
import pandas as pd
import numpy as np
from datetime import datetime, time
 
 
config = configparser.ConfigParser()
config.read("credenciais_banco.ini")
 
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")
 
#gerar query
query_DDV= '''
select cd.Ciclo,emh.PDV ,emh.SKU ,emh.DESCRICAO, emh.CATEGORIA, replace(emh.[DDV PREVISTO],',','.') DDV_PREVISTO  from estoque_mar_historico emh 
inner join ciclos_data_2025 cd on cd.[Date] = emh.data_estoque
inner join (
select distinct data,loja_id, code from draft_historico
) dh on dh.[data] = emh.data_estoque and dh.code = emh.SKU and emh.pdv = dh.loja_id
where emh.CATEGORIA not in ('SUPORTE À VENDA','EMBALAGENS', 'GIFTS') AND emh.DESCRICAO NOT LIKE ('PRM') and emh.ORIGEM  = 'EUD'
and emh.data_estoque in('2025-06-26','2025-07-16','2025-08-06','2025-08-27','2025-09-17') and cd.MARCA ='EUD'
'''
df_ddv2 = pd.read_sql(query_DDV, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\40623521.py:29: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_ddv2 = pd.read_sql(query_DDV, conn)


In [4]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")
 
#gerar query
query_RPT= '''
select 
cd.Ciclo ,emh.PDV ,emh.SKU,count(emh.[ESTOQUE ATUAL] ) dias_em_rpt
FROM estoque_mar_historico emh 
left join ciclos_data_2025 cd on cd.[Date] = emh.data_estoque
where emh.[ESTOQUE ATUAL] =0 and cd.MARCA = 'EUD' and emh.data_estoque > '2025-06-25' and emh.ORIGEM = 'EUD'
group by 
cd.Ciclo ,emh.PDV ,emh.SKU
'''
df_rpt = pd.read_sql(query_RPT, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\3026141127.py:18: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_rpt = pd.read_sql(query_RPT, conn)


In [5]:
df_rpt.head()

Ciclo    PDV    SKU  dias_em_rpt
0  C202511  20997  72793           21
1  C202510  21278  59936            1
2  C202513  20993  55484           21
3  C202515  12820  55956            7
4  C202513  21007  53848           21

In [6]:
df_base= df_base.rename(columns={'loja_id':'PDV','code':'SKU'})

In [7]:
df_ddv = pd.merge(df_base,df_ddv2,on=['Ciclo','PDV','SKU'],how='left')

In [8]:
df_ddv['DDV_PREVISTO'] = df_ddv['DDV_PREVISTO'].astype('float')

In [9]:
df_ruptura = pd.merge(df_ddv,df_rpt,on=['Ciclo','PDV','SKU'],how='left')

df_ruptura['dias_em_rpt'] = df_ruptura['dias_em_rpt'].fillna(0)

df_ruptura.head()

id    PDV    SKU                               description launch  \
0  667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g          
1  667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml          
2  667513  21495  73687                     SOUL DEMAQ CREME 60ML          
3  667527  20997  51775                   EUD BABY SHAMP 200ml V2          
4  667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g          

  deactivation  thirdtolastcyclesales  secondtolastcyclesales  lastcyclesales  \
0                                   0                       0               0   
1          C12                      0                       0               0   
2                                   0                       0               0   
3                                   0                       0               0   
4                                   0                       0               0   

   currentcyclesales  ...  INICIO CICLO   FIM CICLO  DURAÇÃO  MARCA  \
0                  0  ...    25/06/2025  15/07/2025       21    EUD   
1                  0  ...    25/06/2025  15/07/2025       21    EUD   
2                  0  ...    25/06/2025  15/07/2025       21    EUD   
3                  0  ...    25/06/2025  15/07/2025       21    EUD   
4                  0  ...    25/06/2025  15/07/2025       21    EUD   

         Date    id  DESCRICAO  CATEGORIA DDV_PREVISTO dias_em_rpt  
0  25/06/2025  2379        NaN        NaN          NaN         0.0  
1  25/06/2025  2379        NaN        NaN          NaN         0.0  
2  25/06/2025  2379        NaN        NaN          NaN         1.0  
3  25/06/2025  2379        NaN        NaN          NaN         0.0  
4  25/06/2025  2379        NaN        NaN          NaN         0.0  

[5 rows x 46 columns]

In [10]:
df_ruptura['DDV_PREVISTO'] = df_ruptura['DDV_PREVISTO'].replace('None','0')

df_ruptura['DDV_PREVISTO'] = df_ruptura['DDV_PREVISTO'].astype('float')

df_ruptura['DDV_PREVISTO'].sum()

np.float64(16025.960000000001)

In [ ]:
import pyodbc
import configparser
import pandas as pd
import numpy as np
from datetime import datetime, time
 
 
config = configparser.ConfigParser()
config.read("credenciais_banco.ini")
 
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query_vendas = '''
select 
cd.Ciclo ,bvb.PDV ,bvb.sku,replace(bvb.vendas,'.','') as vendas_ciclo
FROM base_vendas_bi bvb
inner join ciclos_data_2025 cd on cd.[Date] = cast(bvb.[DATA] as date)
left join estoque_mar em on em.pdv = bvb.pdv and bvb.sku=em.SKU 
where cd.MARCA = 'EUD' and bvb.[DATA] > '2025-06-24' and em.ORIGEM = 'EUD'

'''
df_vendas2 = pd.read_sql(query_vendas, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\1097998051.py:28: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_vendas2 = pd.read_sql(query_vendas, conn)


In [12]:
df_vendas2['vendas_ciclo'] = df_vendas2['vendas_ciclo'].astype('Int64')

In [13]:
df_vendas = df_vendas2.groupby(['Ciclo','PDV','sku'])['vendas_ciclo'].sum().reset_index()

df_vendas.head()

Ciclo    PDV    sku  vendas_ciclo
0  C202510  20968  59313             4
1  C202510  20968  91715             2
2  C202510  20969  91715             2
3  C202510  20991  91448             0
4  C202510  20991  91540             0

In [14]:
df_vendas2['vendas_ciclo'].sum()

np.int64(20754)

In [15]:
df_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Tabela_Preco\PREÇO VENDA EUDORA.xlsx")

df_preco = df_preco[['Codigo','Venda']]

df_preco = df_preco.rename(columns={'Codigo':'Código','Venda':'Valor'})

df_preco = df_preco.groupby('Código')['Valor'].max().reset_index()

In [16]:
df_preco.head()

Código   Valor
0    1004  159.90
1    1062  226.79
2    1063    1.99
3    1073  226.79
4    1078   67.90

In [17]:
df_vendas['sku'] = df_vendas['sku'].astype('str')

df_vendas.head()

Ciclo    PDV    sku  vendas_ciclo
0  C202510  20968  59313             4
1  C202510  20968  91715             2
2  C202510  20969  91715             2
3  C202510  20991  91448             0
4  C202510  20991  91540             0

In [18]:
df_unificado = pd.merge(df_ruptura,df_vendas,left_on=['Ciclo','PDV','SKU'],right_on=['Ciclo','PDV','sku'],how='left')

df_unificado

id    PDV    SKU                               description  \
0        667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g   
1        667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml   
2        667513  21495  73687                     SOUL DEMAQ CREME 60ML   
3        667527  20997  51775                   EUD BABY SHAMP 200ml V2   
4        667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g   
...         ...    ...    ...                                       ...   
86800  12391049  24269  92676      SOUL PO COMP FAC ULT MATE COR 90 10g   
86801  12391050  24269  92677      SOUL PO COMP FAC ULT MATE COR 95 10g   
86802   9235561  21495  49166                   VOLPE DES COL DNA 100ml   
86803   9235562  21495  52299                  VOLPE DES COL NEXT 100ml   
86804   9235563  21495  56231               VOLPE DES COL TRIUMPH 100ml   

      launch deactivation  thirdtolastcyclesales  secondtolastcyclesales  \
0                                              0                       0   
1                     C12                      0                       0   
2                                              0                       0   
3                                              0                       0   
4                                              0                       0   
...      ...          ...                    ...                     ...   
86800                                          0                       0   
86801                                          0                       0   
86802                                          0                       0   
86803                                          0                       0   
86804                                          0                       0   

       lastcyclesales  currentcyclesales  ...  DURAÇÃO  MARCA        Date  \
0                   0                  0  ...       21    EUD  25/06/2025   
1                   0                  0  ...       21    EUD  25/06/2025   
2                   0                  0  ...       21    EUD  25/06/2025   
3                   0                  0  ...       21    EUD  25/06/2025   
4                   0                  0  ...       21    EUD  25/06/2025   
...               ...                ...  ...      ...    ...         ...   
86800               0                  0  ...       21    EUD  17/09/2025   
86801               0                  0  ...       21    EUD  17/09/2025   
86802               0                  0  ...       21    EUD  27/08/2025   
86803               0                  0  ...       21    EUD  27/08/2025   
86804               0                  0  ...       21    EUD  27/08/2025   

         id                    DESCRICAO   CATEGORIA  DDV_PREVISTO  \
0      2379                          NaN         NaN           NaN   
1      2379                          NaN         NaN           NaN   
2      2379                          NaN         NaN           NaN   
3      2379                          NaN         NaN           NaN   
4      2379                          NaN         NaN           NaN   
...     ...                          ...         ...           ...   
86800  2463                          NaN         NaN           NaN   
86801  2463                          NaN         NaN           NaN   
86802  2442      VOLPE DES COL DNA 100ml  PERFUMARIA          0.02   
86803  2442     VOLPE DES COL NEXT 100ml  PERFUMARIA          0.05   
86804  2442  VOLPE DES COL TRIUMPH 100ml  PERFUMARIA          0.13   

       dias_em_rpt  sku vendas_ciclo  
0              0.0  NaN         <NA>  
1              0.0  NaN         <NA>  
2              1.0  NaN         <NA>  
3              0.0  NaN         <NA>  
4              0.0  NaN         <NA>  
...            ...  ...          ...  
86800          0.0  NaN         <NA>  
86801          0.0  NaN         <NA>  
86802          0.0  NaN         <NA>  
86803          0.0  NaN         <NA>  
8680

In [19]:
df_preco['Código'] = df_preco['Código'].astype('str')

In [20]:
df_unificado = pd.merge(df_unificado,df_preco,left_on=['SKU'],right_on='Código',how='left')


In [21]:
df_unificado=df_unificado.fillna(0)

df_unificado.head()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\2458800028.py:1: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_unificado=df_unificado.fillna(0)


id    PDV    SKU                               description launch  \
0  667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g          
1  667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml          
2  667513  21495  73687                     SOUL DEMAQ CREME 60ML          
3  667527  20997  51775                   EUD BABY SHAMP 200ml V2          
4  667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g          

  deactivation  thirdtolastcyclesales  secondtolastcyclesales  lastcyclesales  \
0                                   0                       0               0   
1          C12                      0                       0               0   
2                                   0                       0               0   
3                                   0                       0               0   
4                                   0                       0               0   

   currentcyclesales  ...        Date    id  DESCRICAO  CATEGORIA  \
0                  0  ...  25/06/2025  2379          0          0   
1                  0  ...  25/06/2025  2379          0          0   
2                  0  ...  25/06/2025  2379          0          0   
3                  0  ...  25/06/2025  2379          0          0   
4                  0  ...  25/06/2025  2379          0          0   

   DDV_PREVISTO  dias_em_rpt  sku  vendas_ciclo Código  Valor  
0           0.0          0.0    0             0  53398  35.99  
1           0.0          0.0    0             0  70882  39.99  
2           0.0          1.0    0             0  73687  32.99  
3           0.0          0.0    0             0  51775  72.98  
4           0.0          0.0    0             0  52332  35.99  

[5 rows x 50 columns]

In [22]:
query_crit = '''SELECT
cd.Ciclo ,                  
dh.loja_id AS PDV,
dh.code as Produto,
COUNT(dh.criticalitem_iscritical  ) AS dias_critico
FROM draft_historico dh
INNER JOIN ciclos_data_2025 cd ON cd.[Date] = dh.[data] AND cd.MARCA ='EUD'
WHERE dh.criticalitem_iscritical  = 1
GROUP BY
cd.Ciclo ,
dh.loja_id,
dh.code'''

df_crit = pd.read_sql(query_crit, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\4239392508.py:14: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_crit = pd.read_sql(query_crit, conn)


In [23]:
df_crit.head()

Ciclo    PDV Produto  dias_critico
0  C202509  22541   40121             1
1  C202509  21001   77773             5
2  C202510  21068   86756            11
3  C202510  21001   77899             1
4  C202515  20997   79483            10

In [24]:
df_crit.shape

(138472, 4)

In [25]:
df_unificado.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA', 'Date', 'id', 'DESCRICAO', 'CATEGORIA', 'DDV_PREVISTO',
       'dias_em_rpt', 'sku', 'vendas_ciclo', 'Código', 'Valor'],
      dtype='object')

In [26]:
df_unificado2 = pd.merge(df_unificado,df_crit, left_on = ['Ciclo','PDV','SKU'], right_on=['Ciclo','PDV','Produto'] ,how='left')

df_unificado2 = df_unificado2.drop(columns='Produto')

df_unificado2['dias_critico'] = df_unificado2['dias_critico'].fillna(0)

df_unificado2.head()

id    PDV    SKU                               description launch  \
0  667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g          
1  667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml          
2  667513  21495  73687                     SOUL DEMAQ CREME 60ML          
3  667527  20997  51775                   EUD BABY SHAMP 200ml V2          
4  667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g          

  deactivation  thirdtolastcyclesales  secondtolastcyclesales  lastcyclesales  \
0                                   0                       0               0   
1          C12                      0                       0               0   
2                                   0                       0               0   
3                                   0                       0               0   
4                                   0                       0               0   

   currentcyclesales  ...    id  DESCRICAO  CATEGORIA  DDV_PREVISTO  \
0                  0  ...  2379          0          0           0.0   
1                  0  ...  2379          0          0           0.0   
2                  0  ...  2379          0          0           0.0   
3                  0  ...  2379          0          0           0.0   
4                  0  ...  2379          0          0           0.0   

   dias_em_rpt  sku  vendas_ciclo  Código  Valor dias_critico  
0          0.0    0             0   53398  35.99          0.0  
1          0.0    0             0   70882  39.99          0.0  
2          1.0    0             0   73687  32.99          0.0  
3          0.0    0             0   51775  72.98          0.0  
4          0.0    0             0   52332  35.99          0.0  

[5 rows x 51 columns]

In [27]:
df_pdv = pd.read_excel('PDV_ATT.xlsx')

In [28]:
df_pdv['PDV'] = df_pdv['PDV'].astype('str')


In [29]:
df_unificado_uf = pd.merge(df_unificado2,df_pdv[['PDV','UF','CANAL']],on='PDV', how='left')
df_unificado_uf.head()

id    PDV    SKU                               description launch  \
0  667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g          
1  667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml          
2  667513  21495  73687                     SOUL DEMAQ CREME 60ML          
3  667527  20997  51775                   EUD BABY SHAMP 200ml V2          
4  667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g          

  deactivation  thirdtolastcyclesales  secondtolastcyclesales  lastcyclesales  \
0                                   0                       0               0   
1          C12                      0                       0               0   
2                                   0                       0               0   
3                                   0                       0               0   
4                                   0                       0               0   

   currentcyclesales  ...  CATEGORIA  DDV_PREVISTO  dias_em_rpt  sku  \
0                  0  ...          0           0.0          0.0    0   
1                  0  ...          0           0.0          0.0    0   
2                  0  ...          0           0.0          1.0    0   
3                  0  ...          0           0.0          0.0    0   
4                  0  ...          0           0.0          0.0    0   

   vendas_ciclo  Código  Valor  dias_critico  UF CANAL  
0             0   53398  35.99           0.0  SE   HIB  
1             0   70882  39.99           0.0  SE   HIB  
2             0   73687  32.99           0.0  SE   HIB  
3             0   51775  72.98           0.0  AL    VD  
4             0   52332  35.99           0.0  SE   HIB  

[5 rows x 53 columns]

In [30]:
df_unificado_uf = df_unificado_uf.rename(columns={'UF':'REGIAO'})
df_unificado_uf.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA', 'Date', 'id', 'DESCRICAO', 'CATEGORIA', 'DDV_PREVISTO',
       'dias_em_rpt', 'sku', 'vendas_ciclo', 'Código', 'Valor', 'dias_critico',
      

In [31]:
df_unificado_uf['UF'] = np.where((df_unificado_uf['REGIAO'] == 'BA3')|(df_unificado_uf['REGIAO'] == 'VDC'),'BA',df_unificado_uf['REGIAO'])

In [32]:
df_unificado_uf.head()

id    PDV    SKU                               description launch  \
0  667507  21495  53398    SOUL BAT MATE MARROM TENDENCIA V2 3,7g          
1  667512  21495  70882  SOUL DELIN LIQ OLHO PRET ESSENCIAL 2,5ml          
2  667513  21495  73687                     SOUL DEMAQ CREME 60ML          
3  667527  20997  51775                   EUD BABY SHAMP 200ml V2          
4  667550  21495  52332    SOUL K/M BAT MATE NUDE AUTORAL V2 3,7g          

  deactivation  thirdtolastcyclesales  secondtolastcyclesales  lastcyclesales  \
0                                   0                       0               0   
1          C12                      0                       0               0   
2                                   0                       0               0   
3                                   0                       0               0   
4                                   0                       0               0   

   currentcyclesales  ...  DDV_PREVISTO  dias_em_rpt  sku  vendas_ciclo  \
0                  0  ...           0.0          0.0    0             0   
1                  0  ...           0.0          0.0    0             0   
2                  0  ...           0.0          1.0    0             0   
3                  0  ...           0.0          0.0    0             0   
4                  0  ...           0.0          0.0    0             0   

   Código  Valor  dias_critico  REGIAO CANAL  UF  
0   53398  35.99           0.0      SE   HIB  SE  
1   70882  39.99           0.0      SE   HIB  SE  
2   73687  32.99           0.0      SE   HIB  SE  
3   51775  72.98           0.0      AL    VD  AL  
4   52332  35.99           0.0      SE   HIB  SE  

[5 rows x 54 columns]

In [33]:
preco_vendas = pd.read_excel(r"compilado preços.xlsx")

In [34]:
preco_vendas.head()

Nome da Origem    chave chave sku1   SKU1   SKU2  \
0  TABELA DE PREÇOS (1).xlsx   1594AL     1594AL   1594   1594   
1  TABELA DE PREÇOS (1).xlsx   1594BA     1594BA   1594   1594   
2  TABELA DE PREÇOS (1).xlsx   1594SE     1594SE   1594   1594   
3  TABELA DE PREÇOS (1).xlsx  17912AL    17912AL  17912  17912   
4  TABELA DE PREÇOS (1).xlsx  17912BA    17912BA  17912  17912   

                       Descrição MARCA  CATEGORIA LINHA  UF Tipo Preço  \
0  QDB MASC CILIO COLEC ROSE 10g   QDB  MAQUIAGEM   QDB  AL     COMPRA   
1  QDB MASC CILIO COLEC ROSE 10g   QDB  MAQUIAGEM   QDB  BA     COMPRA   
2  QDB MASC CILIO COLEC ROSE 10g   QDB  MAQUIAGEM   QDB  SE     COMPRA   
3        QDB BATOM CORALICE 3,8g   QDB  MAQUIAGEM   QDB  AL     COMPRA   
4        QDB BATOM CORALICE 3,8g   QDB  MAQUIAGEM   QDB  BA     COMPRA   

    chave2 chave sku2     PC    PV  
0   AL1594     AL1594  13.55  49.9  
1   BA1594     BA1594  15.26  49.9  
2   SE1594     SE1594   8.26  49.9  
3  AL17912    AL17912   8.12  33.9  
4  BA17912    BA17912   9.14  33.9

In [35]:
preco_vendas = preco_vendas.rename(columns={'SKU2':'Produto'})
preco_vendas.columns

Index(['Nome da Origem', 'chave', 'chave sku1', 'SKU1', 'Produto', 'Descrição',
       'MARCA', 'CATEGORIA', 'LINHA', 'UF', 'Tipo Preço', 'chave2',
       'chave sku2', 'PC', 'PV'],
      dtype='object')

In [36]:
preco_vendas['Produto'] = preco_vendas['Produto'].astype('str')

In [37]:
df_unificado_uf2 = pd.merge(df_unificado_uf,preco_vendas,left_on= ['SKU','UF'],right_on=['Produto','UF'],how='left')



In [38]:
df_unificado_uf2.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA_x', 'Date', 'id', 'DESCRICAO', 'CATEGORIA_x', 'DDV_PREVISTO',
       'dias_em_rpt', 'sku', 'vendas_ciclo', 'Código', 'Valor', 'dias_critico',
  

In [39]:
df_unificado_uf2 = df_unificado_uf2.drop(columns=['Nome da Origem', 'chave', 'chave sku1', 'SKU1', 'Descrição','CATEGORIA_x','CATEGORIA_y', 'LINHA', 'Tipo Preço', 'chave2', 'chave sku2'])

In [40]:
df_unificado_uf2.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA_x', 'Date', 'id', 'DESCRICAO', 'DDV_PREVISTO', 'dias_em_rpt',
       'sku', 'vendas_ciclo', 'Código', 'Valor', 'dias_critico', 'REGIAO',
       

In [41]:
df_unificado_uf2['PRODUTOS_ROMPIDOS_CICLO'] = df_unificado_uf2['DDV_PREVISTO'] * df_unificado_uf2['dias_em_rpt']

In [42]:
df_unificado_uf2['vendas_ciclo'] = df_unificado_uf2['vendas_ciclo'].astype('Int64')

In [43]:
df_unificado_uf2['RECEITA'] = df_unificado_uf2['Valor'] * df_unificado_uf2['vendas_ciclo']

In [44]:
df_unificado_uf2.to_clipboard()

In [45]:
df_unificado_uf2.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA_x', 'Date', 'id', 'DESCRICAO', 'DDV_PREVISTO', 'dias_em_rpt',
       'sku', 'vendas_ciclo', 'Código', 'Valor', 'dias_critico', 'REGIAO',
       

In [46]:
df_unificado_uf2['CAUSA MACRO'] = np.where(df_unificado_uf2['dias_critico'] > 0, "CAUSA INDUSTRIA","")

df_unificado_uf2['Produto_Critico'] = np.where(df_unificado_uf2['dias_critico'] > 0, 1,0)

ANALISAR ITEM CRITICO JUNTO AO MAR.
    - PROCURAR EM PERENE E FAZER O CONCATENADO. :'(
    

In [47]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")


# 1. Puxa fne_pdv (já filtrado)
query_fne = """
SELECT
    fne.cnpj_destinatario,
    fne.cnf AS Nota_Fiscal,
    CAST(fne.data_emissao AS date) AS data_emissao,
    fnei.codigo_pedido,
    fnei.n_item,
    fnei.cod_produto,
    fnei.produto,
    fnei.quantidade,
    fnei.valor_unitario,
    fnei.valor_total_produtos,
    b.PDV
FROM fato_notas_entrada fne
INNER JOIN fato_notas_entrada_itens fnei ON fne.chave = fnei.chave
INNER JOIN base_pdvs b ON fne.cnpj_destinatario = b.CNPJ
WHERE fne.data_emissao > '2025-07-01'
"""
df_fne = pd.read_sql(query_fne, conn)

query_pedidos = """
SELECT
    sellOrders,
    sku,
    storeCode,
    MAX(quantity_accepted) AS quantity_accepted,
    MAX(status) AS status,
    MAX(pedido_id) AS pedido_id,
    MAX(p.[date]) AS [date],
    MAX(deliveryDate) AS deliveryDate,
    cd.Ciclo 
FROM produtos_pedidos p
INNER JOIN ciclos_data_2025 cd on cd.[Date] = p.[date] and cd.MARCA ='BOT'
GROUP BY sellOrders, sku, storeCode, cd.Ciclo 
"""
df_pedidos = pd.read_sql(query_pedidos, conn)

# 3. Puxa draft
query_draft = """
SELECT loja_id, code, salescurve
FROM draft
"""
df_draft = pd.read_sql(query_draft, conn)

# ---- Fazendo os JOINs e agregações em Pandas ----

# JOIN fne com pedidos
df_join = df_fne.merge(df_pedidos, left_on=['codigo_pedido','cod_produto','PDV'],
                       right_on=['sellOrders','sku','storeCode'], how="inner")

# JOIN com draft
df_join = df_join.merge(df_draft, left_on=['PDV','cod_produto'],
                        right_on=['loja_id','code'], how="inner")

# Agrupamento final
df_result = (
    df_join.groupby(['Ciclo','PDV','cod_produto','pedido_id'])
    .agg(
        data_emissao_nf=('data_emissao','max'),
        data_pedido=('date','max'),
        data_prevista_atendimento=('deliveryDate','max'),
        faturado_industria=('quantidade','sum'),
        quantidade_pedida=('quantity_accepted','max'),
        status=('status','max'),
        salescurve=('salescurve','max'),
        valor_total_produtos=('valor_total_produtos','sum'),
        notas=('Nota_Fiscal', lambda x: ', '.join(sorted(set(x)))),
        pedidos=('codigo_pedido', lambda x: ', '.join(sorted(set(x))))
    )
    .reset_index()
)

# Calculando atendimento
df_result['atendimento'] = (
    df_result['faturado_industria'] / df_result['quantidade_pedida'].replace(0, pd.NA)
).round(2)

df_result.head()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\2029767949.py:28: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_fne = pd.read_sql(query_fne, conn)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\2029767949.py:45: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_pedidos = pd.read_sql(query_pedidos, conn)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17416\2029767949.py:52: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft = pd.read_sql(query_draft, conn)


Ciclo    PDV cod_produto pedido_id data_emissao_nf  \
0  C202507  12522       52757   1515922      2025-07-09   
1  C202507  12817       52757   1515918      2025-07-09   
2  C202507  12817       87066   1517306      2025-07-09   
3  C202507  12818       52757   1515924      2025-07-09   
4  C202507  12820       52757   1515943      2025-07-09   

                   data_pedido    data_prevista_atendimento  \
0  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
1  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
2  2025-05-22 00:00:00.0000000  2025-06-13 00:00:00.0000000   
3  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
4  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   

   faturado_industria  quantidade_pedida                 status salescurve  \
0                   5                 35  Parcialmente Atendido          C   
1                  24                 90  Parcialmente Atendido          C   
2                   1                  9              Concluído          C   
3                   4                 25  Parcialmente Atendido          C   
4                   3                 20  Parcialmente Atendido          C   

   valor_total_produtos     notas     pedidos atendimento  
0                 45.36  31953127  0165202706    0.142857  
1                217.71  31754122  0165202491    0.266667  
2                  6.11  31754122  0165206643    0.111111  
3                 36.29  76077782  0165202707        0.16  
4                 27.21  29403846  0165202369        0.15

In [48]:
df_result['PDV'] = df_result['PDV'] .astype('Int64')

df_result['cod_produto'] = df_result['cod_produto'] .astype('Int64')

In [49]:
df_result['PDV'] = df_result['PDV'].astype('str')

df_result['cod_produto'] = df_result['cod_produto'].astype('str')


In [50]:
df_unificado_uf3 = pd.merge(df_unificado_uf2,df_result, left_on= ['Ciclo', 'PDV', 'SKU'],right_on=['Ciclo',	'PDV','cod_produto'],how='left')

In [51]:
df_unificado_uf3['atendimento'].isna().sum()

np.int64(86149)

In [52]:
df_unificado_uf3['atendimento'] = df_unificado_uf3['atendimento'].astype(float)

In [53]:
df_unificado_uf3['VALOR_RPT'] = df_unificado_uf2['PRODUTOS_ROMPIDOS_CICLO'] * df_unificado_uf2['Valor']

In [54]:
df_unificado_uf3[[ 'VALOR_RPT' ,
    'atendimento',
    'atendimento']].dtypes

VALOR_RPT      float64
atendimento    float64
atendimento    float64
dtype: object

In [55]:
df_unificado_uf3.columns

Index(['id', 'PDV', 'SKU', 'description', 'launch', 'deactivation',
       'thirdtolastcyclesales', 'secondtolastcyclesales', 'lastcyclesales',
       'currentcyclesales', 'nextcycleprojection',
       'secondtonextcycleprojection', 'stock_actual', 'stock_intransit',
       'purchasesuggestion', 'smartpurchase_purchasesuggestioncycle',
       'smartpurchase_nextcyclepurchasesuggestion', 'pendingorder',
       'salescurve_x', 'promotions_description', 'promotions_discountpercent',
       'pricesellin', 'businessunit', 'codcategory',
       'criticalitem_dtprovidedregularization', 'criticalitem_blockedwallet',
       'criticalitem_iscritical', 'codsubcategory', 'isproductdeactivated',
       'brandgroupcode', 'dayswithoutsales', 'coveragedays', 'hascoverage',
       'TRIAL949', 'data', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'MARCA_x', 'Date', 'id', 'DESCRICAO', 'DDV_PREVISTO', 'dias_em_rpt',
       'sku', 'vendas_ciclo', 'Código', 'Valor', 'dias_critico', 'REGIAO',
     

In [56]:

# file: scripts/causa_macro_assignment.py
import numpy as np
import pandas as pd

# 1) Sanitize: garantir tipos numéricos coerentes (prevenir strings, vírgulas, etc.)
for c in ['dias_em_rpt', 'VALOR_RPT', 'Produto_Critico', 'atendimento']:
    df_unificado_uf3[c] = pd.to_numeric(df_unificado_uf3[c], errors='coerce')

# 2) Atribuição sequencial (vetorizada, Excel-like)
default = 'Indefinido'
df_unificado_uf3['CAUSA MACRO'] = default

conds_and_values = [
    (df_unificado_uf3['dias_em_rpt'] == 0, 'não houve ruptura'),
    (df_unificado_uf3['dias_critico'] > 0, 'Causa Industria'),
    (df_unificado_uf3['Produto_Critico'] == 1, 'Causa Industria'),
    (df_unificado_uf3['atendimento'].isna(), 'Causa Franqueado'),
    (df_unificado_uf3['atendimento'] < 0.86, 'Causa Industria'),
    (df_unificado_uf3['dias_em_rpt'] > 0, 'Causa Franqueado')    
]

for cond, val in conds_and_values:
    mask = (df_unificado_uf3['CAUSA MACRO'] == default) & cond
    df_unificado_uf3.loc[mask, 'CAUSA MACRO'] = val

# 3) (Opcional) Verificação com apply — igual lógica, mais lenta, útil para debug
def causa_macro_row(row):
    # checagens em ordem — primeira que bater retorna
    if row['dias_em_rpt'] == 0:
        return 'não houve ruptura'
    if row['VALOR_RPT'] == 0:
        return 'não houve ruptura'
    if row['Produto_Critico'] == 1:
        return 'Causa Industria'
    if row['dias_em_rpt'] > 0:
        return 'Causa Franqueado'
    if pd.isna(row['atendimento']):
        return 'Causa Franqueado'
    if row['atendimento'] < 0.86:
        return 'Causa Industria'
    return default

# criar coluna de verificação e comparar (remova após checagem)
df_unificado_uf3['CAUSA_MACRO_check'] = df_unificado_uf3.apply(causa_macro_row, axis=1)
mismatch = df_unificado_uf3[df_unificado_uf3['CAUSA MACRO'] != df_unificado_uf3['CAUSA_MACRO_check']]
print(f"linhas com diferença entre métodos: {len(mismatch)}")
# opcional: df_unificado_uf3.drop(columns=['CAUSA_MACRO_check'], inplace=True)



linhas com diferença entre métodos: 28133


In [57]:

df_unificado_uf3['CAUSA MACRO'].value_counts()

CAUSA MACRO
não houve ruptura    54455
Causa Franqueado     31433
Causa Industria        929
Name: count, dtype: int64

In [58]:
df_unificado_uf3.to_excel(r'C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\Ruptura_Eudora\Rpt_eud-23-10.xlsx',index=False)